In [1]:
import torch
from collections import Counter
import pandas as pd
import plotly.express as px
from sklearn.model_selection import train_test_split
import os
from glob import glob
import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

# Data science tools
import numpy as np
import pandas as pd
import os

# Image manipulations
from PIL import Image

from timeit import default_timer as timer

# Visualizations
import matplotlib.pyplot as plt
%matplotlib inline
plt.rcParams['font.size'] = 14

Matplotlib is building the font cache; this may take a moment.


In [6]:
ImagePATH = f"main_images/"

In [7]:
ImagePATH

'main_images/'

In [8]:

categories = glob(ImagePATH+"*")

In [9]:
print(categories)

['main_images/68', 'main_images/22', 'main_images/70', 'main_images/66', 'main_images/18', 'main_images/31', 'main_images/65', 'main_images/8', 'main_images/28', 'main_images/36', 'main_images/17', 'main_images/25', 'main_images/62', 'main_images/86', 'main_images/27', 'main_images/50', 'main_images/52', 'main_images/78', 'main_images/6', 'main_images/87', 'main_images/83', 'main_images/82', 'main_images/21', 'main_images/12', 'main_images/26', 'main_images/55', 'main_images/73', 'main_images/77', 'main_images/90', 'main_images/71', 'main_images/45', 'main_images/7', 'main_images/63', 'main_images/67', 'main_images/20', 'main_images/33', 'main_images/79', 'main_images/35', 'main_images/10', 'main_images/37', 'main_images/47', 'main_images/75', 'main_images/89', 'main_images/64', 'main_images/32', 'main_images/13', 'main_images/3', 'main_images/60', 'main_images/72', 'main_images/76', 'main_images/0', 'main_images/42', 'main_images/11', 'main_images/84', 'main_images/41', 'main_images/4

In [11]:
filedf = pd.DataFrame()
for cat in categories:
    files = glob(cat+"/*")
    tempdf = pd.DataFrame({'filepath':files,'category':cat.split("/")[-1]})
    filedf = pd.concat([filedf,tempdf])

In [12]:

filedf.head()

filepath category
0  main_images/68/baf64e8767645901.jpg       68
1  main_images/68/a3cb1c941ca6e367.jpg       68
2  main_images/68/d8cbc33026dfb1e0.jpg       68
3  main_images/68/941f693469b4b3a5.jpg       68
4  main_images/68/95b561481a8f6b7a.jpg       68

In [13]:

gby_cnt = filedf.groupby("category").aggregate('count').rename(columns = {'filepath':'cnt'}).reset_index().sort_values(by='cnt',ascending=False)

In [14]:
px.bar(gby_cnt,x = 'category',y = 'cnt',color = 'category',title = 'Counts from Each Category')

In [16]:
!mkdir outputs2

In [17]:

gby_cnt.to_csv(f"outputs/category_counts.csv",index=None)

In [18]:
plt.figure(figsize=(24, 24))

for i in range(16):
    path = filedf.sample(1)['filepath'].values[0]
    category = path.split("/")[1]
    ex_img = Image.open(path)
    ax = plt.subplot(4, 4, i + 1)
    ax.annotate(category, xy=(0.65, 0.9), xycoords="axes fraction",weight='bold',size=20)
    ax.imshow(ex_img)

plt.tight_layout()

In [28]:
focus_cats = gby_cnt[gby_cnt['cnt'] <=20000]['category'].values

In [31]:
focus_cats = gby_cnt[gby_cnt['cnt'] <=20000]['category'].values

In [32]:
filedf  = filedf[filedf['category'].isin(focus_cats)]

In [33]:

filedf.category.value_counts()

6     8157
5     6328
3     5398
4     4771
2     3889
      ... 
33      49
27      44
91      41
32      40
24      40
Name: category, Length: 75, dtype: int64

In [34]:

X_train, X_test, _, _ = train_test_split(
        filedf, filedf['category'],stratify=filedf['category'], test_size=0.4)

X_test, X_val, _, _ = train_test_split(
        X_test, X_test['category'], stratify=X_test['category'], test_size=0.5)

In [35]:
X_train['type'] = 'train'
X_val['type'] = 'val'
X_test['type'] = 'test'

/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [36]:
fulldf = pd.concat([X_train,X_test,X_val])


In [37]:
fulldf.type.value_counts()

train    46239
val      15413
test     15413
Name: type, dtype: int64

In [38]:
fulldf.head()


filepath category   type
5685   main_images/6/c3c73e3898cf3690.jpg        6  train
2541  main_images/87/e1e0e23f1b8e070f.jpg       87  train
2042  main_images/89/aa7ad15e6a35948a.jpg       89  train
3703   main_images/6/c99326ca7b518bb1.jpg        6  train
487   main_images/50/cdcc6dd8146d1639.jpg       50  train

In [39]:

fulldf.category.value_counts()[0]/len(fulldf)

0.10584571465645884

In [40]:

!mkdir data
!rm -rf data/
!rm -rf data/train
!rm -rf data/test
!rm -rf data/val
!mkdir data/
!mkdir data/train
!mkdir data/test
!mkdir data/val


In [41]:
fulldf.category.unique()

array(['6', '87', '89', '50', '34', '78', '84', '68', '5', '9', '2', '63',
       '25', '40', '4', '90', '76', '81', '3', '72', '85', '64', '8',
       '73', '62', '77', '1', '45', '66', '75', '39', '80', '49', '82',
       '57', '7', '55', '83', '86', '88', '70', '23', '29', '38', '11',
       '22', '79', '74', '52', '71', '69', '51', '59', '53', '47', '44',
       '61', '67', '27', '54', '35', '65', '46', '48', '42', '37', '41',
       '30', '60', '33', '91', '36', '32', '24', '17'], dtype=object)

In [42]:

for cat in fulldf.category.unique():
    os.system(f"mkdir data/train/'{cat}'") 
    os.system(f"mkdir data/test/'{cat}'") 
    os.system(f"mkdir data/val/'{cat}'")


In [46]:
fulldf.head()


filepath category   type
5685   main_images/6/c3c73e3898cf3690.jpg        6  train
2541  main_images/87/e1e0e23f1b8e070f.jpg       87  train
2042  main_images/89/aa7ad15e6a35948a.jpg       89  train
3703   main_images/6/c99326ca7b518bb1.jpg        6  train
487   main_images/50/cdcc6dd8146d1639.jpg       50  train

In [45]:

for i,row in fulldf.iterrows():
    # Boat category
    cat = row['category']
    # section is train,val or test
    section = row['type']
    # input filepath to copy
    ipath = row['filepath']
    # output filepath to paste
    opath = ipath.replace(f"images/",f"data/{section}/")
    # running the cp command
    os.system(f"cp '{ipath}' '{opath}'")